In [2]:
import os
os.chdir('/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron')
from hparams import create_hparams
from model import Tacotron2
import torch
from loss_function import Tacotron2Loss
from train import prepare_dataloaders
import waveglow.glow
from waveglow.denoiser import Denoiser
import IPython.display as ipd
import sys
from text import cmudict, text_to_sequence
from data_utils import TextMelLoader, TextMelCollate
import waveglow
import librosa
sys.path.append('waveglow/')
def load_mel(path):
    audio, sampling_rate = librosa.core.load(path, sr=hparams.sampling_rate)
    audio = torch.from_numpy(audio)
    if sampling_rate != hparams.sampling_rate:
        raise ValueError("{} SR doesn't match target {} SR".format(
            sampling_rate, stft.sampling_rate))
    audio_norm = audio.unsqueeze(0)
    audio_norm = torch.autograd.Variable(audio_norm, requires_grad=False)
    melspec = stft.mel_spectrogram(audio_norm)
    melspec = melspec.cuda()
    return melspec

from layers import TacotronSTFT

arpabet_dict = cmudict.CMUDict('data/cmu_dictionary')
waveglow_path = '../../vendor_tools/waveglow/waveglow_256channels_universal_v4.pt'
waveglow = torch.load(waveglow_path)['model'].cuda().eval()
denoiser = Denoiser(waveglow).cuda().eval()
#from glow import infer

/opt/conda/lib/python3.7/site-packages/torch/serialization.py:671: SourceChangeWarning: source code of class 'torch.nn.modules.conv.ConvTranspose1d' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/opt/conda/lib/python3.7/site-packages/torch/serialization.py:671: SourceChangeWarning: source code of class 'torch.nn.modules.container.ModuleList' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/opt/conda/lib/python3.7/site-packages/torch/serialization.py:671: SourceChangeWarning: source code of class 'torch.nn.modules.conv.Conv1d' has changed. you can retrieve the original source code by accessing the object's source attribute or

In [3]:
hparams = create_hparams(None)

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



In [4]:

def load_model(hparams):
    model = Tacotron2(hparams).cuda()
    if hparams.fp16_run:
        model.decoder.attention_layer.score_mask_value = finfo('float16').min

    return model


In [5]:
# hparams.training_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/todos_train.txt'
# hparams.validation_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/todos_val.txt'
hparams.training_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/em_train.txt'
hparams.validation_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/em_val.txt'

hparams.batch_size = 2
hparams.checkpoint_path = '/mnt/disks/uberduck-experiments-v0/models/mellotron/vendor/mellotron_ljs.pt'
hparams.warm_start = True

In [7]:
learning_rate = 1e-3#
from train import warm_start_model

In [64]:
stft = TacotronSTFT(hparams.filter_length, hparams.hop_length, hparams.win_length,
                    hparams.n_mel_channels, hparams.sampling_rate, hparams.mel_fmin,
                    hparams.mel_fmax)

criterion = Tacotron2Loss()
train_loader, valset, collate_fn, train_sampler = prepare_dataloaders(hparams)
iteration = 0
epoch_offset = 0
is_overflow = False

i, batch = next(enumerate(train_loader))


torch.manual_seed(hparams.seed)
model = load_model(hparams)
model = warm_start_model(
    hparams.checkpoint_path, model, hparams.ignore_layers)
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate,weight_decay=hparams.weight_decay)
optimizer.eps = 1e-16

/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


In [66]:
x, y = model.parse_batch(batch)

In [59]:
with torch.no_grad():
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)
    audio = denoiser(waveglow.infer(mel_outputs, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [67]:
for epoch in range(100):
    print("Epoch: {}".format(epoch))
    #start = time.perf_counter()
    model.zero_grad()
    y_pred = model(x)
    loss = criterion(y_pred, y)
    reduced_loss = loss.item()
    loss.backward()
    optimizer.step()
    print(reduced_loss)
    iteration += 1

Epoch: 0
here
1.3669661283493042
Epoch: 1
here
3.15387225151062
Epoch: 2
here
1.8596142530441284
Epoch: 3
here
1.6782375574111938
Epoch: 4
here
1.2177751064300537
Epoch: 5
here
1.0875859260559082
Epoch: 6
here
0.9595178365707397
Epoch: 7
here
0.9037275314331055
Epoch: 8
here
0.8823984861373901
Epoch: 9
here
0.8437399864196777
Epoch: 10
here
0.7722606658935547
Epoch: 11
here
0.7535064220428467
Epoch: 12
here
0.7311992645263672
Epoch: 13
here
0.6999997496604919
Epoch: 14
here
0.6706543564796448
Epoch: 15
here
0.6593843698501587
Epoch: 16
here
0.6347547769546509
Epoch: 17
here
0.6107524633407593
Epoch: 18
here
0.628381609916687
Epoch: 19
here
0.6118065714836121
Epoch: 20
here
0.5645507574081421
Epoch: 21
here
0.5564268231391907
Epoch: 22
here
0.5537024736404419
Epoch: 23
here
0.5348937511444092
Epoch: 24
here
0.5222367644309998
Epoch: 25
here
0.5089238882064819
Epoch: 26
here
0.504401445388794
Epoch: 27
here
0.5072682499885559
Epoch: 28
here
0.5059694647789001
Epoch: 29
here
0.48424622416

In [68]:
with torch.no_grad():
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)
    audio = denoiser(waveglow.infer(mel_outputs, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

here


In [72]:
i, batch = next(enumerate(train_loader))
x, y = model.parse_batch(batch)
with torch.no_grad():
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)
    audio = denoiser(waveglow.infer(mel_outputs, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


here


In [8]:
# hparams.training_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/todos_train.txt'
# hparams.validation_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/todos_val.txt'
hparams.training_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/em_train.txt'
hparams.validation_files = '/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/experiments/filelists/em_val.txt'

hparams.batch_size = 16
hparams.checkpoint_path = '/mnt/disks/uberduck-experiments-v0/models/mellotron/vendor/mellotron_ljs.pt'
hparams.warm_start = True

stft = TacotronSTFT(hparams.filter_length, hparams.hop_length, hparams.win_length,
                    hparams.n_mel_channels, hparams.sampling_rate, hparams.mel_fmin,
                    hparams.mel_fmax)

criterion = Tacotron2Loss()
train_loader, valset, collate_fn, train_sampler = prepare_dataloaders(hparams)
iteration = 0
epoch_offset = 0
is_overflow = False

learning_rate = 1e-3#

torch.manual_seed(hparams.seed)
model = load_model(hparams)
model = warm_start_model(
    hparams.checkpoint_path, model, hparams.ignore_layers)
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate,weight_decay=hparams.weight_decay)
optimizer.eps = 1e-16

Warm starting model from checkpoint '/mnt/disks/uberduck-experiments-v0/models/mellotron/vendor/mellotron_ljs.pt'


In [9]:
for epoch in range(5):
    for i, batch in enumerate(train_loader):
        print(epoch,i)
        x, y = model.parse_batch(batch)
        model.zero_grad()
        y_pred = model(x)
        loss = criterion(y_pred, y)
        reduced_loss = loss.item()
        loss.backward()
        optimizer.step()

/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


0 0
here
0 1
here
0 2
here
0 3
here
0 4
here
0 5
here
0 6
here
0 7
here
0 8
here
0 9
here
0 10
here
0 11
here
0 12
here
0 13
here
0 14
here
0 15
here
0 16
here
0 17
here
0 18
here
0 19
here
0 20
here
0 21
here
0 22
here
0 23
here
0 24
here
0 25
here
0 26
here
0 27
here


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


1 0
here
1 1
here
1 2
here
1 3
here
1 4
here
1 5
here
1 6
here
1 7
here
1 8
here
1 9
here
1 10
here
1 11
here
1 12
here
1 13
here
1 14
here
1 15
here
1 16
here
1 17
here
1 18
here
1 19
here
1 20
here
1 21
here
1 22
here
1 23
here
1 24
here
1 25
here
1 26
here
1 27
here


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


2 0
here
2 1
here
2 2
here
2 3
here
2 4
here
2 5
here
2 6
here
2 7
here
2 8
here
2 9
here
2 10
here
2 11
here
2 12
here
2 13
here
2 14
here
2 15
here
2 16
here
2 17
here
2 18
here
2 19
here
2 20
here
2 21
here
2 22
here
2 23
here
2 24
here
2 25
here
2 26
here
2 27
here


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


3 0
here
3 1
here
3 2
here
3 3
here
3 4
here
3 5
here
3 6
here
3 7
here
3 8
here
3 9
here
3 10
here
3 11
here
3 12
here
3 13
here
3 14
here
3 15
here
3 16
here
3 17
here
3 18
here
3 19
here
3 20
here
3 21
here
3 22
here
3 23
here
3 24
here
3 25
here
3 26
here
3 27
here


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


4 0
here
4 1
here
4 2
here
4 3
here
4 4
here
4 5
here
4 6
here
4 7
here
4 8
here
4 9
here
4 10
here
4 11
here
4 12
here
4 13
here
4 14
here
4 15
here
4 16
here
4 17
here
4 18
here
4 19
here
4 20
here
4 21
here
4 22
here
4 23
here
4 24
here
4 25
here
4 26
here
4 27
here


In [10]:
with torch.no_grad():
    model.zero_grad()
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)
    audio = denoiser(waveglow.infer(mel_outputs, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

here


In [14]:
i, batch = next(enumerate(valset))
print(epoch,i)
x, y = model.parse_batch(batch)
model.zero_grad()
with torch.no_grad():
    model.zero_grad()
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)
    audio = denoiser(waveglow.infer(mel_outputs, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

4 0


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


ValueError: not enough values to unpack (expected 7, got 4)

In [ ]:
with torch.no_grad():
    audio = denoiser(waveglow.infer(mel_outputs_postnet, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [30]:
with torch.no_grad():
    audio = denoiser(waveglow.infer(y[0], sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [40]:
for epoch in range(100):
    print("Epoch: {}".format(epoch))
    #start = time.perf_counter()
    model.zero_grad()
    y_pred = model(x)
    loss = criterion(y_pred, y)
    reduced_loss = loss.item()
    loss.backward()
    optimizer.step()
    print(reduced_loss)
    iteration += 1

Epoch: 0
here
59.34856033325195
Epoch: 1
here
40.65153503417969
Epoch: 2
here
21.910377502441406
Epoch: 3
here
10.1885404586792
Epoch: 4
here
6.714853286743164
Epoch: 5
here
7.989645481109619
Epoch: 6
here
8.815452575683594
Epoch: 7
here
8.379119873046875
Epoch: 8
here
7.426441669464111
Epoch: 9
here
6.590748310089111
Epoch: 10
here
6.167103290557861
Epoch: 11
here
5.906838417053223
Epoch: 12
here
5.814554214477539
Epoch: 13
here
5.809908390045166
Epoch: 14
here
5.891162872314453
Epoch: 15
here
5.820067405700684
Epoch: 16
here
5.790283679962158
Epoch: 17
here
5.680721759796143
Epoch: 18
here
5.5428900718688965
Epoch: 19
here
5.4404988288879395
Epoch: 20
here
5.328752517700195
Epoch: 21
here
5.305197715759277
Epoch: 22
here
5.2411980628967285
Epoch: 23
here
5.248751163482666
Epoch: 24
here
5.198711395263672
Epoch: 25
here
5.176126480102539
Epoch: 26
here
5.087698459625244
Epoch: 27
here
5.086284637451172
Epoch: 28
here
5.023273468017578
Epoch: 29
here
4.971691608428955
Epoch: 30
here
4.

In [41]:
print(y_pred[0].shape,y_pred[1].shape,y_pred[2].shape,y_pred[3].shape)
print(y[0].shape,y[1].shape )#no y[2], y[3]
print(x[0].shape,x[1].shape,x[2].shape, x[3], x[4], x[5],x[6].shape)

(torch.Size([1, 80, 345]), torch.Size([1, 345]))

In [14]:
#audio_paths = 'data/examples_filelist.txt'
audio_paths = hparams.training_files
dataloader = TextMelLoader(audio_paths, hparams)
datacollate = TextMelCollate(1)

file_idx = 0
audio_path, text, sid = dataloader.audiopaths_and_text[file_idx]

# get audio path, encoded text, pitch contour and mel for gst
text_encoded = torch.LongTensor(text_to_sequence(text, hparams.text_cleaners, arpabet_dict))[None, :].cuda()    
pitch_contour = dataloader[file_idx][3][None].cuda()
mel = load_mel(audio_path)
print(audio_path, text)

# load source data to obtain rhythm using tacotron 2 as a forced aligner
#x, y = model.parse_batch(datacollate([dataloader[file_idx]]))

/mnt/disks/uberduck-experiments-v0/data/uberduck/eminem/wav/112.wav five rounds. And murder you hoes worse than a convertible flippin vertical, Nose-first with the top off landing upside-down.


/mnt/disks/uberduck-experiments-v0/uberduck-ml-dev/src/vendor_run/mellotron/yin.py:44: RuntimeWarning: invalid value encountered in true_divide
  cmndf = df[1:] * range(1, N) / np.cumsum(df[1:]).astype(float) #scipy method


In [15]:
with torch.no_grad():
    # get rhythm (alignment map) using tacotron 2
    mel_outputs, mel_outputs_postnet, gate_outputs, rhythm = model.forward(x)
    rhythm = rhythm.permute(1, 0, 2)

here


In [16]:
with torch.no_grad():
    audio = denoiser(waveglow.infer(mel_outputs_postnet, sigma=0.8), 0.01)[:, 0]

In [17]:
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [118]:
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [115]:
# speaker_id = torch.LongTensor([1]).cuda()
# mel_outputs, mel_outputs_postnet, gate_outputs, _ = model.inference_noattention(
#     (text_encoded, mel, speaker_id,pitch_contour, rhythm))

In [80]:
from numba import cuda 
cuda.select_device(0)
cuda.close()

In [110]:
with torch.no_grad():
    audio = denoiser(waveglow.infer(mel_outputs_postnet, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [52]:
#i think this was on this x batch
with torch.no_grad():
    audio = denoiser(waveglow.infer(mel_outputs_postnet, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)

In [101]:
#i think this was on the em x batch.... incredibly good for a model trained on eminem and transferred to 'space'
with torch.no_grad():
    audio = denoiser(waveglow.infer(mel_outputs_postnet, sigma=0.8), 0.01)[:, 0]
ipd.Audio(audio[0].data.cpu().numpy(), rate=hparams.sampling_rate)